# Setup

In [1]:
# %pip install -q -r requirements.txt

## Config

In [2]:
INPUT_DATASET = 'derek-thomas/labeled-multiple-choice-explained-mistral-reasoning'
REVISION = '536f3b8'
OUTPUT_DATASET = 'derek-thomas/labeled-multiple-choice-explained-mistral-tokenized'

In [3]:
from transformers import AutoTokenizer
from huggingface_hub import get_token, login

login()

In [4]:
BASE_MODEL = 'mistralai/Mistral-7B-Instruct-v0.3'
tokenizer = AutoTokenizer.from_pretrained(BASE_MODEL, token=get_token())

# Prompt Experiment
## Goal
I want to explore a few scenarios for prompt fine-tuning. Lets consider a scenario where we have the following available:
- (Q) Question
- (AC) Answer Choices
- (R) Reasoning
- (FA) Final Answer

How would performance differ if we tried changing the order?

Scenario 1: `Q - AC - R - FA`
This is the most natural, we want the model to generate reasoning before the final answer. Based on how decoding works, this will give the most information before selecting the Final Answer.

Scenario 2: `Q - AC - FA - R`
This is quite awkward. Why would we put our reasoning last? Its faster. Could the model be trained in such a way to "know" the reasoning before responding with it? If so we could save a lot of tokens. Im skeptical, but its worth testing.

Scenario 3: `Q - AC - FA`
This is our fine-tuning control.

Scenario 4: Base
This is our un-fine-tuned control.

In each of these scenarios I will build prompts with strucutred generation to fine-tune with. I noticed some difficulty in a first pass with getting consistent response formats, but thats out of scope, so structured generation can help a lot here.

Datasets wont store complex structures like lists of dicts of different types (needed for structured generation, so its easiest if I tokenize. Ill be using Mistral, so Ill skip the system prompt. Its simple enough to come back and change this for a different model in this notebook.

## Implementation
To explore this goal, we will start with [layoric/labeled-multiple-choice-explained](https://huggingface.co./datasets/layoric/labeled-multiple-choice-explained) as our dataset. It has explanations already provided by GPT-3.5-turbo. Given that these explanations are a bit different than what mistral would do, it might be useful if we generate some from mistral as well. Based on [this notebook](./poe-generate-mistral-reasoning.ipynb) we have been able to generate mistral reasoning in this refined dataset [derek-thomas/labeled-multiple-choice-explained-mistral-reasoning](https://huggingface.co./datasets/derek-thomas/labeled-multiple-choice-explained-mistral-reasoning).

In this notebook we will format our data such that we can try each experiment and then we will push it to my repo: [derek-thomas/labeled-multiple-choice-explained](https://huggingface.co./datasets/derek-thomas/labeled-multiple-choice-explained).

## Imports

In [5]:
import pandas as pd
from datasets import load_dataset
import json

## Load and Preprocess the Dataset

In [6]:
# Load dataset from Hugging Face Hub
dataset = load_dataset(INPUT_DATASET, split='train')

# Convert to pandas dataframe
df = dataset.to_pandas()
print(f"Before Cleaning: {len(df)} rows")

# Drop the __index_level_0__ column if it exists
df.drop(columns=['mistral_reasoning_prompt'], errors='ignore', inplace=True)

# Ensure all values in 'formatted_question' are strings
df.rename(columns={
    'explanation': 'gpt3_5_reasoning',
}, inplace=True)
df

Before Cleaning: 8413 rows


formatted_question  \
0     what is satellite technology used for predicti...   
1     what does irradiating food do? (a) relieve pai...   
2     what protects a mammal's skin? (a) fiber folli...   
3     what do earthworms do when a segment breaks of...   
4     lightning can be bad for what? (a) the environ...   
...                                                 ...   
8408  organisms that can cause infection do what? (a...   
8409   fungi are living things that cannot make thei...   
8410  an overheated body can use water for: (a) meta...   
8411  what is essential for cellular respiration for...   
8412  what helps insulate and protect the body? (a) ...   

                                          combined_fact answer_key  \
0     satellite technology is used for predicting wh...          c   
1                 irradiated food improves food safety.          c   
2                   fiber follicles protect mammal skin          a   
3         earthworms can regrow segments that break off          b   
4             lightning can be bad for the environment.          a   
...                                                 ...        ...   
8408  organisms that can cause infection make humans...          g   
8409  fungi are living things that cannot make their...          a   
8410  the evaporation of water from the skin cools t...          g   
8411  plants are essential for cellular respiration ...          f   
8412  living cells in follicles help insulate and pr...          b   

             topic                                   gpt3_5_reasoning  \
0       Technology  a) Seconds and minutes: This option is incorre...   
1     Food science  (a) Relieve pain: This option is not correct b...   
2          Biology  b) Exfoliation: Exfoliation is the process of ...   
3          Biology  a) Dies: This option is not correct because ea...   
4      Electricity  b) Rainstorms: Lightning is actually a natural...   
...            ...                                                ...   
8408       Biology  a) Bandaging open sores is not the correct ans...   
8409       Biology  b) Fungi are living things that can make their...   
8410       Biology  a) Metabolic reaction: This option is incorrec...   
8411       Biology  a) Electrons are involved in cellular respirat...   
8412       Biology  a) H2O: Water is essential for life, but it do...   

                                          question_text  \
0     What is satellite technology used for predicting?   
1                        What does irradiating food do?   
2                        What protects a mammal's skin?   
3      What do earthworms do when a segment breaks off?   
4                        Lightning can be bad for what?   
...                                                 ...   
8408        Organisms that can cause infection do what?   
8409  Fungi are living things that cannot make their...   
8410             An overheated body can use water for:?   
8411  What is essential for cellular respiration for...   
8412          What helps insulate and protect the body?   

                                         answer_choices  \
0     (a) Seconds and minutes (b) The strength and m...   
1     (a) Relieve pain (b) Enhance food's nutrients ...   
2     (a) Fiber follicles (b) Exfoliation (c) Resist...   
3     (a) Dies (b) Regrows it (c) Reproduces (d) Sed...   
4     (a) The environment (b) Rainstorms (c) Destruc...   
...                                                 ...   
8408  (a) Bandage open sores (b) Keep flesh clean (c...   
8409  (a) Food (b) Cells (c) Energy (d) Fruits (e) H...   
8410  (a) Metabolic reaction (b) Dehydrating (c) Rai...   
8411  (a) Electron (b) Glucose (c) Energy (d) Energy...   
8412  (a) H2o (b) Living cells in follicles (c) Laye...   

                                      mistral_reasoning  
0     Incorrect answers and explanations:\n\n1. Elec...  
1     Sure, let's examine each answer and justify wh...  
2     Sure, let's 

## Create Prompts from Processed Data

We need to convert our sample into a format similar to below for each of the scenarios.

```
[
    {"content": user_content, "role": "user"},
    {"content": assistant_response, "role": "assistant"}
]
```

We should include a helpful system_prompt with a general trivia prefix, and a suffix that contains instructions that fit each scenario.
The `user_content` will have the Question and answer choices.
The `assistant_response` should reflect the scenario. 

In [7]:
df['user_prompt'] = df.apply(lambda row: f"Question: {row['question_text']}\nAnswer Choices: {row['answer_choices']}", axis=1)

Here we need to create the structure of our conversation. Each system prompt should reflect the instructions we want, so we can start with a prefix and add in the specifics for each scenario.

### Reasoning Final Answer Structured Generation

In [8]:
# Define system prompt
system_prompt_RFA = 'Answer the Question and include your Reasoning and the Final Answer in a json like: {"Reasoning: "...", "Final Answer": "x"} where x is a letter that corresponds to the answer choice which is a letter between a and h.'

df['assistant_prompt_RFA_gpt3_5'] = df.apply(lambda row: {"Reasoning": row["gpt3_5_reasoning"].strip(), "Final Answer": row["answer_key"]}, axis=1)
df['assistant_prompt_RFA_mistral'] = df.apply(lambda row: {"Reasoning": row["mistral_reasoning"].strip(), "Final Answer": row["answer_key"]}, axis=1)

# Step 1: Create user prompt for both gpt3_5 and mistral
df['user_prompt_RFA'] = df.apply(lambda row: {
    "content": system_prompt_RFA + '\n' + row['user_prompt'],
    "role": "user"
}, axis=1)

# Step 2: Create conversation_RFA column using user_prompt_RFA
df['conversation_RFA_gpt3_5'] = df.apply(lambda row: tokenizer.apply_chat_template([
    row['user_prompt_RFA'],  # Use the precomputed user prompt
    {"content": row['assistant_prompt_RFA_gpt3_5'], "role": "assistant"}
], tokenize=False), axis=1)

df['conversation_RFA_mistral'] = df.apply(lambda row: tokenizer.apply_chat_template([
    row['user_prompt_RFA'],  # Use the precomputed user prompt
    {"content": row['assistant_prompt_RFA_mistral'], "role": "assistant"}
], tokenize=False), axis=1)

df['user_prompt_RFA'] = df['user_prompt_RFA'].apply(lambda row: tokenizer.apply_chat_template([row], tokenize=False))

df.drop(['assistant_prompt_RFA_gpt3_5', 'assistant_prompt_RFA_mistral'], inplace=True, axis=1)

# Example output
gpt3_5_example = df['conversation_RFA_gpt3_5'].iloc[0]
mistral_example = df['conversation_RFA_mistral'].iloc[0]

print(gpt3_5_example)
print('\n\n')
print(mistral_example)

<s>[INST] Answer the Question and include your Reasoning and the Final Answer in a json like: {"Reasoning: "...", "Final Answer": "x"} where x is a letter that corresponds to the answer choice which is a letter between a and h.
Question: What is satellite technology used for predicting?
Answer Choices: (a) Seconds and minutes (b) The strength and magnitude of an earthquake (c) What it's like outside each day (d) 70-75 degrees fahrenheit (e) Rapid changes occur (f) Dead-ends and false starts. (g) Snow, ice, and rock (h) Around 5 to 27 degrees celsius[/INST] {'Reasoning': "a) Seconds and minutes: This option is incorrect because satellite technology is not used for predicting time intervals. Satellite technology is used for various purposes such as communication, navigation, and weather forecasting, but it is not used for predicting time intervals.\n\nb) The strength and magnitude of an earthquake: This option is incorrect because satellite technology is not used for predicting earthquak

### Final Answer Reasoning Structured Generation

In [9]:
system_prompt_FAR = 'Answer the Question and include your Final Answer and the Reasoning in a json like: {"Final Answer": "x", "Reasoning: "..."} where x is a letter that corresponds to the answer choice which is a letter between a and h.'

df['assistant_prompt_FAR_gpt3_5'] = df.apply(lambda row: {"Final Answer": row["answer_key"], "Reasoning": row["gpt3_5_reasoning"].strip()}, axis=1)
df['assistant_prompt_FAR_mistral'] = df.apply(lambda row: {"Final Answer": row["answer_key"], "Reasoning": row["mistral_reasoning"].strip()}, axis=1)

# Step 1: Create user_prompt_FAR column
df['user_prompt_FAR'] = df.apply(lambda row: {
    "content": system_prompt_FAR + '\n' + row['user_prompt'],
    "role": "user"
}, axis=1)

# Step 2: Create conversation_FAR column using user_prompt_FAR
df['conversation_FAR_gpt3_5'] = df.apply(lambda row: tokenizer.apply_chat_template([
    row['user_prompt_FAR'],  # Use the precomputed user prompt
    {"content": row['assistant_prompt_FAR_gpt3_5'], "role": "assistant"}
], tokenize=False), axis=1)

df['conversation_FAR_mistral'] = df.apply(lambda row: tokenizer.apply_chat_template([
    row['user_prompt_FAR'],  # Use the precomputed user prompt
    {"content": row['assistant_prompt_FAR_mistral'], "role": "assistant"}
], tokenize=False), axis=1)

df['user_prompt_FAR'] = df['user_prompt_FAR'].apply(lambda row: tokenizer.apply_chat_template([row], tokenize=False))

df.drop(['assistant_prompt_FAR_gpt3_5', 'assistant_prompt_FAR_mistral'], inplace=True, axis=1)

# Example output
gpt3_5_example = df['conversation_FAR_gpt3_5'].iloc[0]
mistral_example = df['conversation_FAR_mistral'].iloc[0]

print(gpt3_5_example)
print('\n\n')
print(mistral_example)

<s>[INST] Answer the Question and include your Final Answer and the Reasoning in a json like: {"Final Answer": "x", "Reasoning: "..."} where x is a letter that corresponds to the answer choice which is a letter between a and h.
Question: What is satellite technology used for predicting?
Answer Choices: (a) Seconds and minutes (b) The strength and magnitude of an earthquake (c) What it's like outside each day (d) 70-75 degrees fahrenheit (e) Rapid changes occur (f) Dead-ends and false starts. (g) Snow, ice, and rock (h) Around 5 to 27 degrees celsius[/INST] {'Final Answer': 'c', 'Reasoning': "a) Seconds and minutes: This option is incorrect because satellite technology is not used for predicting time intervals. Satellite technology is used for various purposes such as communication, navigation, and weather forecasting, but it is not used for predicting time intervals.\n\nb) The strength and magnitude of an earthquake: This option is incorrect because satellite technology is not used for

### Final Answer Structured Generation

In [10]:
system_prompt_FA = 'Answer the Question and include your Final Answer in a json like: {"Final Answer": "x"} where x is a letter that corresponds to the answer choice which is a letter between a and h.'
df['assistant_prompt_FA'] = df.apply(lambda row: {"Final Answer": row["answer_key"]}, axis=1)

# Step 1: Create user_prompt_FA column
df['user_prompt_FA'] = df.apply(lambda row: {
    "content": system_prompt_FA + '\n' + row['user_prompt'],
    "role": "user"
}, axis=1)

# Step 2: Create conversation_FA_R column using user_prompt_FA
df['conversation_FA'] = df.apply(lambda row: tokenizer.apply_chat_template([
    row['user_prompt_FA'],  # Use the precomputed user prompt
    {"content": row['assistant_prompt_FA'], "role": "assistant"}
    # {"content": json.dumps(row['assistant_prompt_FA']), "role": "assistant"}
], tokenize=False), axis=1)


df['user_prompt_FA'] = df['user_prompt_FA'].apply(lambda row: tokenizer.apply_chat_template([row], tokenize=False))

df.drop(['assistant_prompt_FA'], inplace=True, axis=1)


# Example output
example = df['conversation_FA'].iloc[0]

print(example)

<s>[INST] Answer the Question and include your Final Answer in a json like: {"Final Answer": "x"} where x is a letter that corresponds to the answer choice which is a letter between a and h.
Question: What is satellite technology used for predicting?
Answer Choices: (a) Seconds and minutes (b) The strength and magnitude of an earthquake (c) What it's like outside each day (d) 70-75 degrees fahrenheit (e) Rapid changes occur (f) Dead-ends and false starts. (g) Snow, ice, and rock (h) Around 5 to 27 degrees celsius[/INST] {'Final Answer': 'c'}</s>


### Cleanup

In [11]:
df.columns

Index(['formatted_question', 'combined_fact', 'answer_key', 'topic',
       'gpt3_5_reasoning', 'question_text', 'answer_choices',
       'mistral_reasoning', 'user_prompt', 'user_prompt_RFA',
       'conversation_RFA_gpt3_5', 'conversation_RFA_mistral',
       'user_prompt_FAR', 'conversation_FAR_gpt3_5',
       'conversation_FAR_mistral', 'user_prompt_FA', 'conversation_FA'],
      dtype='object')

In [12]:
df = df[['topic', 'question_text', 'answer_key', 'gpt3_5_reasoning', 'mistral_reasoning', 'answer_choices', 'user_prompt', 
         'user_prompt_RFA', 'conversation_RFA_gpt3_5', 'conversation_RFA_mistral',
         'user_prompt_FAR', 'conversation_FAR_gpt3_5', 'conversation_FAR_mistral',
         'user_prompt_FA', 'conversation_FA']]

In [13]:
df

topic                                      question_text  \
0       Technology  What is satellite technology used for predicting?   
1     Food science                     What does irradiating food do?   
2          Biology                     What protects a mammal's skin?   
3          Biology   What do earthworms do when a segment breaks off?   
4      Electricity                     Lightning can be bad for what?   
...            ...                                                ...   
8408       Biology        Organisms that can cause infection do what?   
8409       Biology  Fungi are living things that cannot make their...   
8410       Biology             An overheated body can use water for:?   
8411       Biology  What is essential for cellular respiration for...   
8412       Biology          What helps insulate and protect the body?   

     answer_key                                   gpt3_5_reasoning  \
0             c  a) Seconds and minutes: This option is incorre...   
1             c  (a) Relieve pain: This option is not correct b...   
2             a  b) Exfoliation: Exfoliation is the process of ...   
3             b  a) Dies: This option is not correct because ea...   
4             a  b) Rainstorms: Lightning is actually a natural...   
...         ...                                                ...   
8408          g  a) Bandaging open sores is not the correct ans...   
8409          a  b) Fungi are living things that can make their...   
8410          g  a) Metabolic reaction: This option is incorrec...   
8411          f  a) Electrons are involved in cellular respirat...   
8412          b  a) H2O: Water is essential for life, but it do...   

                                      mistral_reasoning  \
0     Incorrect answers and explanations:\n\n1. Elec...   
1     Sure, let's examine each answer and justify wh...   
2     Sure, let's go through each of the provided an...   
3     1. Reading the question carefully, we can see ...   
4     1. Food: While essential for the growth and he...   
...                                                 ...   
8408  1. Read the question and options carefully: Th...   
8409  1. Read the question and options carefully: Th...   
8410  1. Read the question and options carefully: Th...   
8411  1. First, let's read the question and options ...   
8412  1. Read the question and options carefully: Th...   

                                         answer_choices  \
0     (a) Seconds and minutes (b) The strength and m...   
1     (a) Relieve pain (b) Enhance food's nutrients ...   
2     (a) Fiber follicles (b) Exfoliation (c) Resist...   
3     (a) Dies (b) Regrows it (c) Reproduces (d) Sed...   
4     (a) The environment (b) Rainstorms (c) Destruc...   
...                                                 ...   
8408  (a) Bandage open sores (b) Keep flesh clean (c...   
8409  (a) Food (b) Cells (c) Energy (d) Fruits (e) H...   
8410  (a) Metabolic reaction (b) Dehydrating (c) Rai...   
8411  (a) Electron (b) Glucose (c) Energy (d) Energy...   
8412  (a) H2o (b) Living cells in follicles (c) Laye...   

                                            user_prompt  \
0     Question: What is satellite technology used fo...   
1     Question: What does irradiating food do?\nAnsw...   
2     Question: What protects a mammal's skin?\nAnsw...   
3     Question: What do earthworms do when a segment...   
4     Question: Lightning can be bad for what?\nAnsw...   
...                                                 ...   
8408  Question: Organisms that can cause infection d...   
8409  Question: Fungi are living things that cannot ...   
8410  Question: An overheated body can use water for...   
8411  Question: What is essential for cellular respi...   
8412  Question: What helps insulate and protect the ...   

                                        user_prompt_RFA  \
0     <s>[INST] Answer the Question and include your...   
1     <s>[INST] Answer the Question and include yo

## Explore Prompts
Gradio can be really useful for quick inline apps. Here I want to make sure everything is as I expect.

While the above print statements helped me see the format, the gradio app helps me explore a large volume of output easily. 

Note: Its tricky as I cant easily render newlines in strings. So be careful!

In [14]:
import json
import gradio as gr

# Gradio app to browse prompts with left and right buttons
# index = 0

# Functions to handle prompts
def get_prompt(index, prompt_type):
    return df.iloc[index][prompt_type]

def next_prompt(index, prompt_type):
    if index < len(df) - 1:
        index += 1
    return index, get_prompt(index, prompt_type)

def previous_prompt(index, prompt_type):
    if index > 0:
        index -= 1
    return index, get_prompt(index, prompt_type)

# Gradio App
with gr.Blocks() as demo:
    gr.Markdown("# Prompt Browser")
    with gr.Row():
        prompt_type_dropdown = gr.Dropdown(
            choices=['conversation_RFA_gpt3_5', 'conversation_RFA_mistral', 'conversation_FAR_gpt3_5', 'conversation_FAR_mistral', 'conversation_FA_gpt3_5', 'conversation_FA_mistral'],
            value='conversation_RFA_gpt3_5',
            label="Select Prompt Type"
        )
        index_display = gr.Textbox("0", label="Index", interactive=False)

    prompt_display = gr.Textbox(value=df.iloc[0]['conversation_RFA_gpt3_5'], label="Prompt")
    
    with gr.Row():
        prev_button = gr.Button("⬅️ Previous")
        next_button = gr.Button("Next ➡️")
    
    # State to hold the current index
    index_state = gr.State(value=0)

    # Button click events
    prev_button.click(
        fn=previous_prompt,
        inputs=[index_state, prompt_type_dropdown],
        outputs=[index_state, prompt_display]
    )
    next_button.click(
        fn=next_prompt,
        inputs=[index_state, prompt_type_dropdown],
        outputs=[index_state, prompt_display]
    )

    # Dropdown change event
    prompt_type_dropdown.change(
        fn=lambda index, prompt_type: get_prompt(index, prompt_type),
        inputs=[index_state, prompt_type_dropdown],
        outputs=prompt_display
    )

    # Update index display
    index_state.change(
        fn=lambda index: str(index),
        inputs=index_state,
        outputs=index_display
    )

# Launch the app
demo.launch(height=840)

* Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.


## Push Dataset to the Hub
Its useful to get a train, test split, then we convert to `Dataset` and push to the hub. We also want to stratify on `'topic'`.

In [15]:
from datasets import Dataset, DatasetDict
from sklearn.model_selection import train_test_split

# First split to create train and remaining (val + test)
train_df, test_df = train_test_split(df, test_size=0.2, stratify=df['topic'], random_state=42)

# Reset index to avoid index column in the Hugging Face Dataset
train_df.reset_index(drop=True, inplace=True)
test_df.reset_index(drop=True, inplace=True)

# Convert each DataFrame to a Dataset object
train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)

# Create a DatasetDict with the train, validation, and test datasets
dataset_dict = DatasetDict({
    'train': train_dataset,
    'test': test_dataset
})

In [16]:
# Push the dataset to the Hugging Face Hub
dataset_dict.push_to_hub(OUTPUT_DATASET)

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/7 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/2 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co./datasets/derek-thomas/labeled-multiple-choice-explained-mistral-tokenized/commit/f96a8487961dcfe6077df67b5351c041a4523eb1', commit_message='Upload dataset', commit_description='', oid='f96a8487961dcfe6077df67b5351c041a4523eb1', pr_url=None, repo_url=RepoUrl('https://huggingface.co./datasets/derek-thomas/labeled-multiple-choice-explained-mistral-tokenized', endpoint='https://huggingface.co.', repo_type='dataset', repo_id='derek-thomas/labeled-multiple-choice-explained-mistral-tokenized'), pr_revision=None, pr_num=None)